Three methods of calculating the center coordinates of a watch face are shown in this file.
Mesh data is taken from 'clean_wrist.obj' and 'worn_wrist.obj

In [1]:
pip install trimesh

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [2]:
pip install rtree

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


Utils:
These functions will be used in the proposed methods. These are functions that are frequesntly used. 

In [16]:
#This method aligns mesh2 with mesh1 
# It uses the iterative closest point (ICP) algorithm for point cloud registration from the trimesh library for finding the optimal transformation
def alignMeshes(mesh1,mesh2):
  points1 = mesh1.vertices 
  points2 = mesh2.vertices 

  # Compute the transformation matrix to align mesh2 with mesh1
  matrix, _, _ = trimesh.registration.icp(points2, points1,max_iterations=500)

  # Apply the transformation matrix to mesh2
  mesh2_aligned = mesh2.copy()
  mesh2_aligned.apply_transform(matrix)
  return mesh2_aligned

#this methods gives center coordinates of the 3D point cloud
def GetCenter(watchDialMesh):
  # watchDialMesh from previous cell or also can be imported from .obj file.
  cloud = watchDialMesh

  # Estimate surface normal using oriented point sampling
  radius = 0.1
  k = 6
  tree = KDTree(cloud.vertices)
  indices = tree.query_radius(cloud.vertices, r=radius, return_distance=False)
  normals = []
  for i, p in enumerate(cloud.vertices):
      if len(indices[i]) < k:
          continue
      cov = np.cov(cloud.vertices[indices[i]].T)
      evals, evecs = np.linalg.eigh(cov)
      idx = np.argsort(evals)[::-1]
      normal = evecs[:, idx[2]]
      if np.dot(normal, p - cloud.vertices[indices[i][0]]) < 0:
          normal *= -1
      normals.append(normal)
  cloud.vertex_normals = np.array(normals)

  # Project point cloud onto plane defined by surface normal
  plane_origin = np.mean(cloud.vertices, axis=0)
  plane_normal = np.mean(cloud.vertex_normals, axis=0)
  projected_cloud = cloud.vertices - np.outer((cloud.vertices - plane_origin).dot(plane_normal), plane_normal)

  # Compute convex hull of projected point cloud
  convex_hull = trimesh.convex.ConvexHull(projected_cloud)

  # Compute centroid of convex hull to find center of bottom face
  center = np.mean(projected_cloud[convex_hull.vertices], axis=0)
  bottom_center = np.dot(center - plane_origin, plane_normal) * plane_normal + plane_origin
  return bottom_center


Implementation of Method 1: Bounding box method

1. First align the clean_wrist mesh to the worn_wrist mesh so that all the cordinates will be in the reference of worn_wrist.
2. get the radius, height and the transformation matrix using the minimum bounding cylinder to the aligned clean_wrist mesh. This way we know the span of the wrist and its radius. 
3. Create sphere and bounding box and use the transformation matrix to align them with the aligned clean wrist mesh. This way only the points of the dial are left out of the bounding boxes. (A cylindrical bounding box can also be used instead of sphere and box)
4. Now find the points that are outside the bounding box and the sphere.
5. Now this is like inverted plate shaped point cloud. Using PCA get the axis(surface normal) to the bottom of the inverted plate and project the points to this plane.
6. Compute convex hull of projected point cloud. Calculate the center by taking mean of the convex hull projected points.

In [4]:
import trimesh
import numpy as np

# Load the meshes
clean_wrist_mesh = trimesh.load('clean_wrist.obj')
worn_wrist_mesh = trimesh.load('worn_wrist.obj')

#Align clean_wrist_mesh with worn_wrist_mesh 
clean_wrist_mesh_aligned = alignMeshes(worn_wrist_mesh,clean_wrist_mesh)

color1 = [1.0, 0.0, 0.0, 1.0]  # Red color
color2 = [0.0, 1.0, 0.0, 1.0]  # Green color
clean_wrist_mesh.visual.vertex_colors = color1
clean_wrist_mesh_aligned.visual.vertex_colors = color1
worn_wrist_mesh.visual.vertex_colors = color2

# Display
scene1 = trimesh.Scene()
scene1.add_geometry(clean_wrist_mesh_aligned)
scene1.add_geometry(worn_wrist_mesh)
scene1.show()

In [5]:
#Creating bounding boxes
# distances = np.linalg.norm(point_cloud.vertices[:, None] - point_cloud.vertices, axis=-1)
# max_distance = np.max(distances)
max_distance = 93 #from running above two lines.

cylinderVal = trimesh.bounds.minimum_cylinder(clean_wrist_mesh_aligned)

# Print cylinder properties
print("Radius: ", cylinderVal['radius'])
radius = cylinderVal['radius']
print("Height: ", cylinderVal['height'])
height =  cylinderVal['height']
print("transform: ", cylinderVal['transform'])
rotation_matrix = cylinderVal['transform']

# Create a cylinder,sphere mesh using the height and radius
# Cylinder is created but not used. It can also be used instead of sphere.
scalingFactor=1.05
cylinder = trimesh.creation.cylinder(radius=radius*scalingFactor, height=height*scalingFactor)
sphere = trimesh.creation.uv_sphere(radius=radius*scalingFactor)
print(radius*scalingFactor,height*scalingFactor)
to_origin, extents = trimesh.bounds.oriented_bounds(clean_wrist_mesh_aligned)
print(to_origin)

#create axis for better understanding the transformations
axis_lines = trimesh.creation.axis(10)

color = [0.0, 1.0, 0.0, 0.5]  # Green color with alpha 0.5
cylinder.visual.face_colors = [color] * len(cylinder.faces)
cylinder.apply_transform(to_origin)
# Translate the cylinder,sphere,box to the adjust the orientation of the point cloud
#the blue axis is the z-axis, the green axis is the y-axis, and the red axis is the x-axis.
cylinder.apply_translation([ -80.00000000e+00,  -22.00000000e+00,  59.00000000e+00])
sphere.apply_translation([ -30.00000000e+00,  -5.00000000e+00,  54.50000000e+00])

bbox = trimesh.creation.box(extents=extents*1.2, transform=rotation_matrix)
bbox.apply_translation([ 0.00000000e+00,  0.00000000e+00,  0.50000000e+00])

#Display
# scene = trimesh.Scene([clean_wrist_mesh_aligned, worn_wrist_mesh, cylinder,axis_lines,bbox,sphere])
scene = trimesh.Scene([clean_wrist_mesh_aligned, worn_wrist_mesh,axis_lines,sphere,bbox])
scene.show()


Radius:  38.70589824964508
Height:  75.57447048861073
transform:  [[-3.16349539e-01  7.17547502e-03 -9.48615560e-01 -2.40916837e+01]
 [ 2.27001666e-03  9.99974256e-01  6.80694250e-03 -1.29537384e+01]
 [ 9.48639982e-01  0.00000000e+00 -3.16357684e-01  5.28688294e+01]
 [ 0.00000000e+00  0.00000000e+00  0.00000000e+00  1.00000000e+00]]
40.64119316212734 79.35319401304127
[[ 0.38764735  0.1229395  -0.91357288 55.48724344]
 [ 0.91236587 -0.19265564  0.36120952  6.65805001]
 [-0.13159805 -0.97353463 -0.18684825 -0.58149494]
 [ 0.          0.          0.          1.        ]]


In [6]:
#Finding points outside the bounding box
# Get the vertices of the point cloud
vertices = worn_wrist_mesh.vertices

# Vertices that are inside the bounding box
inside_bbox = bbox.contains(vertices)
# Vertices that are inside the sphere
inside_sphere = sphere.contains(vertices)

# Find the vertices that are outside both the bounding box and the sphere
outside = ~(inside_bbox | inside_sphere)

# Get the points that are outside the bounding box and outside the sphere
points_outside = vertices[outside]

print(len(points_outside))
# create trimesh from the points
outside_mesh = trimesh.Trimesh(np.array(points_outside))
# Export to check in CloudCompare
#outside_mesh.export('outside_points.obj')

2547


In [7]:
from sklearn.neighbors import KDTree
#Get the center of the watch face from the outsde_mesh found previously
bottom_center1 = GetCenter(outside_mesh)
print("Watch face center:", bottom_center1)

Watch face center: [-12.3756317    2.00839508  19.29822446]


**Implementation of Method 2:**

1. Step 1 remains same as method 1, where we align the clean_wrist mesh to the worn_wrist_mesh. 
2. Using appropriate threshold values for the distances of the points in worn_wrist_mesh that are not close enough to any point in clean_wrist_mesh_aligned we can get the top face points of the watch.
3. Step 3 is similar to step 5 and 6 in method 1.
 This method can be improved by using clustering methods.
 


In [8]:
import trimesh
import numpy as np

# Load the meshes
clean_wrist_mesh = trimesh.load('clean_wrist.obj')
worn_wrist_mesh = trimesh.load('worn_wrist.obj')

#Align clean_wrist_mesh with worn_wrist_mesh 
clean_wrist_mesh_aligned = alignMeshes(worn_wrist_mesh,clean_wrist_mesh)

In [9]:
num_vertices_aligned = len(worn_wrist_mesh.vertices)
num_vertices_original = len(clean_wrist_mesh_aligned.vertices)
print(num_vertices_aligned)
print(num_vertices_original)
threshold = 10  # Change this to adjust the threshold

# Find the points in worn_wrist_mesh that are not close enough to any point in clean_wrist_mesh_aligned
extra_points = []
for point in worn_wrist_mesh.vertices:
    distances = np.linalg.norm(clean_wrist_mesh_aligned.vertices - point, axis=1)
    if np.min(distances) > threshold:
        extra_points.append(point)

# Create a new mesh using the extra points
extra_mesh = trimesh.Trimesh(vertices=extra_points)
# Plot the extra mesh
color1 = [1.0, 0.0, 0.0, 1.0]  # Red color
extra_mesh.visual.vertex_colors = color1
extra_mesh.show(background=True)
extra_mesh.show()
extra_mesh.export("extra_mesh.obj")


17311
13368


'# https://github.com/mikedh/trimesh\nv -18.12411308 -5.03688288 13.66548920 1.00000000 0.00000000 0.00000000\nv -15.63759804 -6.88310623 14.56640816 1.00000000 0.00000000 0.00000000\nv -20.51791763 0.26674300 13.17127991 1.00000000 0.00000000 0.00000000\nv -13.14569378 -8.83643723 15.41957283 1.00000000 0.00000000 0.00000000\nv -15.66157627 -6.06316090 14.72299099 1.00000000 0.00000000 0.00000000\nv -16.32604790 -6.43322611 14.34509563 1.00000000 0.00000000 0.00000000\nv -13.18800545 -9.62711906 15.23228168 1.00000000 0.00000000 0.00000000\nv -13.80828094 -9.17860222 15.02026939 1.00000000 0.00000000 0.00000000\nv -15.71335411 -5.22768211 14.89455414 1.00000000 0.00000000 0.00000000\nv -15.01783752 -5.71514606 15.07119083 1.00000000 0.00000000 0.00000000\nv -15.65340900 -7.70663595 14.42103577 1.00000000 0.00000000 0.00000000\nv -14.98743153 -6.50993395 14.90242672 1.00000000 0.00000000 0.00000000\nv -16.32280159 -5.57461500 14.52248287 1.00000000 0.00000000 0.00000000\nv -14.35326385

In [10]:
from sklearn.neighbors import KDTree
#Get the center of the watch face from the outsde_mesh found previously
bottom_center2 = GetCenter(extra_mesh)
print("Watch face center:", bottom_center2)

Watch face center: [-13.25752659   8.75680113  22.46645845]


**Implementation of Method 3:**

This method gives the most closest answer to the actual center of the watch face.

1. Same as method 1, align the clean_wrist with the worn_wrist mesh.
2. Using trimesh.proximity.signed_distance get the points that are outside the clean wrist. This way we get the entire watch points. 
3. Using LocalOutlierFactor from sklearn.neigbors remove the outlier points that are away from the wrist watch point cloud.
4. Create a cylindrical bounding box on the inliner points mesh. Align the cylinder such that only watch dial points are outside of it.
5. Similar to step 5 and 6 in method 1. 
Now this is like inverted plate shaped point cloud. Using PCA get the axis(surface normal) to the bottom of the inverted plate and project the points to this plane.
Compute convex hull of projected point cloud. Calculate the center by taking mean of the convex hull projected points.


In [11]:
import trimesh
import numpy as np

# Load the meshes
clean_wrist_mesh = trimesh.load('clean_wrist.obj')
worn_wrist_mesh = trimesh.load('worn_wrist.obj')

#Align clean_wrist_mesh with worn_wrist_mesh 
clean_wrist_mesh_aligned = alignMeshes(worn_wrist_mesh,clean_wrist_mesh)

color1 = [1.0, 0.0, 0.0, 1.0]  # Red color
color2 = [0.0, 1.0, 0.0, 1.0]  # Green color
clean_wrist_mesh.visual.vertex_colors = color1
clean_wrist_mesh_aligned.visual.vertex_colors = color1
worn_wrist_mesh.visual.vertex_colors = color2

# Compute the signed distance from each point on clean_wrist_mesh_aligned to worn_wrist_mesh
distances = trimesh.proximity.signed_distance(clean_wrist_mesh_aligned, worn_wrist_mesh.vertices)
# Extract the points on worn_wrist_mesh that are outside clean_wrist_mesh_aligned
# points that are outside will have negative signs
outside_points = worn_wrist_mesh.vertices[distances < 0]
print(len(outside_points))
# Create a new mesh object from the outside points
outside_mesh = trimesh.Trimesh(outside_points)
outside_mesh.export('outside_mesh.obj')

9191


'# https://github.com/mikedh/trimesh\nv -18.12411308 -5.03688288 13.66548920\nv -15.63759804 -6.88310623 14.56640816\nv -20.51791763 0.26674300 13.17127991\nv -13.14569378 -8.83643723 15.41957283\nv -15.66157627 -6.06316090 14.72299099\nv -16.32604790 -6.43322611 14.34509563\nv -13.18800545 -9.62711906 15.23228168\nv -13.80828094 -9.17860222 15.02026939\nv -15.71335411 -5.22768211 14.89455414\nv -15.01783752 -5.71514606 15.07119083\nv -15.65340900 -7.70663595 14.42103577\nv -14.98743153 -6.50993395 14.90242672\nv -16.32280159 -5.57461500 14.52248287\nv -14.35326385 -6.20790195 15.22136784\nv -16.34017944 -7.26253223 14.18302155\nv -14.42728233 -5.39319420 15.38956642\nv -12.51041412 -8.51060867 15.83283615\nv -15.11071873 -4.88772297 15.24416256\nv -12.51597404 -9.30862617 15.64152908\nv -15.01300240 -7.33514977 14.75942230\nv -13.78660202 -8.36709690 15.17446899\nv -13.14743710 -8.03284168 15.56414986\nv -14.36015320 -6.99996090 15.08094978\nv -15.70143318 -8.54414082 14.26190281\nv -

In [12]:
import numpy as np
from sklearn.neighbors import LocalOutlierFactor
# Load point cloud data
point_cloud = outside_points
print(len(point_cloud))

# Set LOF parameters
n_neighbors = 800
contamination = 0.15

# Fit LOF model to the data
lof = LocalOutlierFactor(n_neighbors=n_neighbors, contamination=contamination)
outlier_labels = lof.fit_predict(point_cloud)

# Identify inliers and outliers
inlier_mask = outlier_labels == 1
outlier_mask = outlier_labels == -1
inliers = point_cloud[inlier_mask]
outliers = point_cloud[outlier_mask]

# Create a new mesh using the extra points
inliers_mesh = trimesh.Trimesh(inliers)
inliers_mesh.export("inliers_mesh.obj")

9191


'# https://github.com/mikedh/trimesh\nv -18.12411308 -5.03688288 13.66548920\nv -15.63759804 -6.88310623 14.56640816\nv -20.51791763 0.26674300 13.17127991\nv -13.14569378 -8.83643723 15.41957283\nv -15.66157627 -6.06316090 14.72299099\nv -16.32604790 -6.43322611 14.34509563\nv -13.18800545 -9.62711906 15.23228168\nv -13.80828094 -9.17860222 15.02026939\nv -15.71335411 -5.22768211 14.89455414\nv -15.01783752 -5.71514606 15.07119083\nv -15.65340900 -7.70663595 14.42103577\nv -14.98743153 -6.50993395 14.90242672\nv -16.32280159 -5.57461500 14.52248287\nv -14.35326385 -6.20790195 15.22136784\nv -16.34017944 -7.26253223 14.18302155\nv -14.42728233 -5.39319420 15.38956642\nv -12.51041412 -8.51060867 15.83283615\nv -15.11071873 -4.88772297 15.24416256\nv -12.51597404 -9.30862617 15.64152908\nv -15.01300240 -7.33514977 14.75942230\nv -13.78660202 -8.36709690 15.17446899\nv -13.14743710 -8.03284168 15.56414986\nv -14.36015320 -6.99996090 15.08094978\nv -15.70143318 -8.54414082 14.26190281\nv -

In [13]:
#Creating bounding boxes
# distances = np.linalg.norm(point_cloud.vertices[:, None] - point_cloud.vertices, axis=-1)
# max_distance = np.max(distances)
max_distance = 93 #from running above two lines. #Just for reference to get idea of the dimensions

cylinderVal = trimesh.bounds.minimum_cylinder(inliers_mesh)

radius = cylinderVal['radius']
height =  cylinderVal['height']
rotation_matrix = cylinderVal['transform']

#inliers_mesh
points = inliers_mesh.vertices

# Define parameters for cylinder creation
scalingfactor = 1.58
# radius = 54.5
# height = 100.0

origin = [-75.00000000e+00,  -5.00000000e+00,  45.80000000e+00]
endpoint = [ 15,         -10,  95       ]
# Create cylinder mesh using principal axis as direction
cylinder_mesh = trimesh.creation.cylinder(radius=radius*scalingfactor, height=height*scalingfactor, segment=[origin, endpoint])
axis_mesh = trimesh.creation.axis(10)

scene = trimesh.Scene([worn_wrist_mesh,cylinder_mesh,axis_mesh])
scene.show()

In [14]:
#Finding points outside the cylinder
# Get the vertices
vertices = inliers_mesh.vertices

# Vertices that are inside the cylinder_mesh 
inside_cylinder = cylinder_mesh.contains(vertices)

# Find the vertices that are outside both the cylinder_mesh 
outside = ~(inside_cylinder)

# Get the points that are outside
points_outside = vertices[outside]

print(len(points_outside))
# create trimesh from the points
outside_mesh = trimesh.Trimesh(np.array(points_outside))
# Export and check in CloudCompare
#outside_mesh.export('outside_points.obj')

2143


In [15]:
from sklearn.neighbors import KDTree
#Get the center of the watch face from the outsde_mesh found previously
bottom_center3 = GetCenter(outside_mesh)
print("Watch face center:", bottom_center3)

Watch face center: [-11.32102835   3.13580067  19.55048049]
